In [4]:
import pandas as pd
import torch
from transformers import AutoTokenizer, AutoModel
import re

In [2]:
# Target列を分割する関数
def split_target(target):
    # 指定された区切り文字で分割
    split_words = re.split(r'[,\n、・及びおよび又はまたは]+', target)
    # 空白文字を除外してリストとして返す
    return [word.strip() for word in split_words if word.strip()]

In [3]:
basedf = pd.read_csv('../ClinicalTrialCSV/JRCT20241202Cancer.csv', index_col=0)
basedf = basedf.dropna(subset=['試験等のフェーズ'])
# Target列を分割してTargetWord列を追加
basedf['TargetWord'] = basedf['Target'].apply(split_target)

In [5]:
# モデルとトークナイザーのロード
model_name = "intfloat/multilingual-e5-large"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

tokenizer_config.json:   0%|          | 0.00/418 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/690 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

In [6]:
# テキストをベクトル化する関数
def encode_text(texts):
    inputs = tokenizer(texts, padding=True, truncation=True, return_tensors="pt")
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.last_hidden_state.mean(dim=1)  # 平均プーリングでベクトル化

In [66]:
# クエリ
query = "乳がん"
#query = "神経膠腫"
threshold = 0.91
#threshold = 0.875
# クエリをベクトル化
query_vec = encode_text([query])

In [67]:
query_vec.shape

torch.Size([1, 1024])

In [68]:
# ターゲットリスト全体を処理
matched_indices = []
target_vecs_list = []
cosine_scores_list = []
for idx, target_words in enumerate(basedf['TargetWord']):
    # ターゲット内の各単語をベクトル化
    target_vecs = encode_text(target_words)
    # コサイン類似度を計算
    cosine_scores = torch.nn.functional.cosine_similarity(query_vec, target_vecs)
    target_vecs_list.append(target_vecs)
    cosine_scores_list.append(cosine_scores)
    # 閾値を超えるか確認
    if (cosine_scores >= threshold).any():  # いずれかが閾値を超えている場合
        matched_indices.append(idx)

# 抽出
matched_df = basedf.iloc[matched_indices]
matched_df

JRCT ID       NCT No JapicCTI No  \
12   jRCT2041240130          NaN         NaN   
59   jRCT2031240404          NaN         NaN   
201  jRCT2052240059          NaN         NaN   
234  jRCT2031240065          NaN         NaN   
257  jRCT2033240023          NaN         NaN   
271  jRCT2031230750  NCT06188559         NaN   
279  jRCT2031230723  NCT06112379         NaN   
311  jRCT2061230102  NCT06103864         NaN   
396  jRCT2061230074  NCT05952557         NaN   
467  jRCT2031230249  NCT05753501         NaN   
509  jRCT2031230109  NCT05514054         NaN   
514  jRCT2031230090          NaN         NaN   
515  jRCT2031230096  NCT05774951         NaN   
582  jRCT2051220176          NaN         NaN   
610  jRCT2061220087  NCT05629585         NaN   
693  jRCT2031220276  NCT05307705         NaN   
708  jRCT2031220203          NaN         NaN   
753  jRCT2031220034  NCT04862663         NaN   
802  jRCT2031210585  NCT05123482         NaN   
865  jRCT2052210099          NaN         NaN   

                                                 Title  \
12   中等度-高度PONV発症リスクを有する肺切除術予定患者の周術期管理におけるGranisetr...   
59   転移性HR+/HER2-乳がん及びその他の進行性固形がん患者を対象にCDK4阻害剤BGB-4...   
201  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...   
234  DNAミスマッチ修復機構欠損を有する進行性・転移性子宮体がん患者を対象に、一次治療として化学...   
257  免疫チェックポイント阻害剤に対してacquired resistanceとなったがん患者を対...   
271  治療歴のある HER2 陽性又は HER2 低発現の切除不能又は転移性乳癌の被験者を対象に，...   
279  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...   
311  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...   
396  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...   
467  [M23-647]B細胞性悪性腫瘍患者を対象としたBTK 分解誘導化合物ABBV-101 の...   
509  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...   
514  MELK阻害剤OTS167POにおける転移性・進行性乳がん患者を対象とした安全性、忍容性およ...   
515  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...   
582  切除不能進行再発食道がん及び胃がんに対する免疫チェックポイント阻害剤(ICI)と光線力学的療...   
610  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...   
693  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...   
708  初回腫瘍減量手術肉眼的完全切除後の進行卵巣癌を対象にパクリタキセル、カルボプラチン投与後のニ...   
753  局所進行（切除不能）又は転移性のホルモン受容体陽性／ヒト上皮細胞成長因子受容体2 陰性乳癌を...   
802  進行又は転移性固形がん患者を対象としたAZD8205の単独療法及び他の抗がん剤との併用療法に...   
865  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...   

                                                Target  \
12                                                 肺がん   
59   ・進行性固形腫瘍・進行性乳がん・転移性乳がん・ホルモン受容体陽性乳がん・ホルモン受容体陽性乳...   
201                                                乳がん   
234                                              子宮体がん   
257                                  肺がん、食道がん、胃癌等の固形がん   
271                     HER2 陽性又は HER2 低発現の切除不能又は転移性乳癌   
279                                                 乳癌   
311                                                 乳癌   
396                                          乳がん、早期乳がん   
467                                               血液がん   
509                                                 乳癌   
514                  再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん   
515                                          乳がん、早期乳がん   
582                                           食道がん、胃がん   
610                                                 乳癌   
693                                                乳がん   
708                                               卵巣がん   
753                                  局所進行（切除不能）又は転移性乳癌   
802                                   乳癌、胆道癌、卵巣癌、子宮内膜癌   
865                                                乳がん   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  \
12   全身麻酔を要する肺切除術周術期における標準制吐療法であるグラニセトロン(Granisetro...        2   NaN   
59   サイクリン依存性キナーゼ 4 (CDK4) 阻害剤である BGB-43395 が、ホルモン受...        1   NaN   
201  HSD17B4高メチル化（HSD17B4 hypermethylation：HH）を有するH...        2   NaN   
234  dMMR/MSI-Hを有する再発又は進行子宮体癌患者を対象にdostarlimabの有効性及...        3   NaN   
257  免疫チェックポイント阻害剤に対してacquired resistanceとなったがん患者（非...      1-2   NaN   
271                                                 治療        2   NaN   
279  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...

In [69]:
cosine_scores_list

[tensor([0.8485]),
 tensor([0.8322, 0.8710]),
 tensor([0.8630]),
 tensor([0.8748, 0.8663]),
 tensor([0.9373]),
 tensor([0.8615, 0.8576]),
 tensor([0.8443]),
 tensor([0.8511]),
 tensor([0.8320, 0.8452]),
 tensor([0.8485]),
 tensor([0.8681]),
 tensor([0.8585]),
 tensor([0.8489]),
 tensor([0.8535]),
 tensor([0.9058]),
 tensor([0.8473, 0.9020]),
 tensor([0.8587]),
 tensor([0.8621]),
 tensor([0.8526]),
 tensor([0.8363]),
 tensor([0.8573]),
 tensor([0.7646, 0.7990]),
 tensor([0.9068, 0.8733, 0.8775]),
 tensor([0.8584]),
 tensor([0.8584]),
 tensor([0.8624]),
 tensor([0.8456]),
 tensor([0.8959]),
 tensor([0.8844]),
 tensor([0.8842, 0.9356, 0.9305, 0.9065, 0.8970]),
 tensor([0.8691, 0.8630, 0.8718]),
 tensor([0.8758]),
 tensor([0.8630]),
 tensor([0.8611]),
 tensor([0.8630]),
 tensor([0.8963]),
 tensor([0.8601]),
 tensor([0.8040, 0.8439]),
 tensor([0.8789, 0.8568]),
 tensor([0.8110, 0.8643, 0.8400, 0.9012]),
 tensor([0.8604]),
 tensor([0.8752, 0.8826, 0.8916, 0.8565]),
 tensor([0.9091, 0.8941, 0

In [70]:
# 全データのターゲット列をベクトル化
target_list = basedf['Target'].tolist()

target_vecs = encode_text(target_list)
    # コサイン類似度を計算
cosine_scores = torch.nn.functional.cosine_similarity(query_vec, target_vecs)

In [71]:
matched_indices_d = (cosine_scores >= threshold).nonzero().tolist()
# 入れ子リストをフラットなリストに変換
flat_indices_d = [idx[0] for idx in matched_indices_d]

# 抽出
matched_df_d = basedf.iloc[flat_indices_d]
matched_df_d


JRCT ID       NCT No JapicCTI No  \
12   jRCT2041240130          NaN         NaN   
201  jRCT2052240059          NaN         NaN   
279  jRCT2031230723  NCT06112379         NaN   
311  jRCT2061230102  NCT06103864         NaN   
396  jRCT2061230074  NCT05952557         NaN   
509  jRCT2031230109  NCT05514054         NaN   
515  jRCT2031230096  NCT05774951         NaN   
610  jRCT2061220087  NCT05629585         NaN   
693  jRCT2031220276  NCT05307705         NaN   
865  jRCT2052210099          NaN         NaN   

                                                 Title     Target  \
12   中等度-高度PONV発症リスクを有する肺切除術予定患者の周術期管理におけるGranisetr...        肺がん   
201  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...        乳がん   
279  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...         乳癌   
311  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...         乳癌   
396  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...  乳がん、早期乳がん   
509  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...         乳癌   
515  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...  乳がん、早期乳がん   
610  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...         乳癌   
693  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...        乳がん   
865  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...        乳がん   

                                              研究・治験の目的 試験等のフェーズ 試験の種類    無作為化  \
12   全身麻酔を要する肺切除術周術期における標準制吐療法であるグラニセトロン(Granisetro...        2   NaN  無作為化比較   
201  HSD17B4高メチル化（HSD17B4 hypermethylation：HH）を有するH...        2   NaN     単一群   
279  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...        3   NaN  無作為化比較   
311  PD-L1陽性の局所再発手術不能または転移性TNBC患者を対象に、デュルバルマブ併用または非...        3   NaN  無作為化比較   
396                                          Treatment        3   NaN  無作為化比較   
509            早期乳癌患者を対象としたimlunestrantと標準的な内分泌療法の比較試験        3   NaN  無作為化比較   
515                                          Treatment        3   NaN  無作為化比較   
610  術前薬物療法後の外科的切除時に乳房および／または腋窩リンパ節に浸潤性残存病変を有するI～II...        3   NaN  無作為化比較   
693  LOXO-783 の単独投与及び他の抗がん剤との併用投与における 第 2 相試験の推奨用量、...        1   NaN     単一群   
865  本治験の目的は，乳がん又はその疑いのある者，並びに乳がん又はその疑いがない者を対象に乳房画像...        2   NaN     単一群   

     盲検化  ...             purpose  \
12   非盲検  ...   treatment purpose   
201  非盲検  ...  diagnostic purpose   
279  非盲検  ...   treatment purpose   
311  非盲検  ...   treatment purpose   
396  非盲検  ...   treatment purpose   
509  非盲検  ...   treatment purpose   
515  非盲検  ...   treatment purpose   
610  非盲検  ...   treatment purpose   
693  非盲検  ...   treatment purpose   
865  単盲検  ...           screening   

                                    Inclusion Criteria  \
12   (1) Patients scheduled to undergo anatomical l...   
201  1. Histologically confirmed invasive breast ca...   
279  1. Participant must be >= 18 years at the time...   
311  Histologically or cytologically documented loc...   
396  - Women and Men; 18 years or more at the time ...   
509  -Have a diagnosis of ER+, HER2- early-stage, r...   
515  - Women and Men, greater than or equal to 18 y...   
610  Participant must be >= 18 years at the time of...   
693  -Have advanced breast cancer or another solid ...   
865  Breast cancer (including suspected) \r\n(1) On...   

                                    Exclusion Criteria     Age Minimum  \
12   (1) Patients with a history of allergy to the ...  18age old over   
201  1. History of other malignancy within the last...  20age old over   
279  1. As judged by the investigator, any evidence...  18age old over   
311  As judged by investigator, severe or uncontrol...  18age old over   
396  - Inoperable locally advanced or metastatic br...  18age old over   
509  -Have any evidence of metastatic disease (incl...  18age old over   
515  - Inoperable locally advanced or metastatic br...  18age old over   
610  Stage IV (metastatic) TNBC.\r\nHistory of prio...  18age old over   
693  -Medical Conditions\r\n -Colorectal cancer\r\n...  18age old over   
865  (1) There is trauma with bleeding on th